In [1]:
!pip install -q tensorflow_recommenders
!pip install -q ScaNN

     |████████████████████████████████| 85 kB 2.6 MB/s 
     |████████████████████████████████| 462 kB 42.6 MB/s 
     |████████████████████████████████| 10.9 MB 5.1 MB/s 


In [ ]:
from google.colab import files
files.upload()

Saving jinxpro.csv to jinxpro.csv


{'jinxpro.csv': b'User_ID,Product_ID,Ratings\r\n9ef432eb6251297304e76186b10a928d,4244733e06e7ecb4970a6e2683c13e61,4\r\nb0830fb4747a6c6d20dea0b8c802d7ef,e5f2d52b802189ee658865ca93d83a8f,5\r\n41ce2a54c0b03bf3443c3d931a367089,c777355d18b72b67abbeef9df44fd0fd,5\r\nf88197465ea7920adcdbec7375364d82,7634da152a4610f1595efa32f14722fc,5\r\n8ab97904e6daea8866dbdbc4fb7aad2c,ac6c3623068f30de03045865e4e10089,5\r\n503740e9ca751ccdda7ba28e9ab8f608,ef92defde845ab8450f9d70c526ef70f,1\r\ned0271e0b7da060a393796590e7b737a,8d4f2bb7e93e6710a28f34fa83ee7d28,5\r\n9bdf08b4b3b52b5526ff42d37d47f222,557d850972a7d6f792fd18ae1400d9b6,5\r\nf54a9f0e6b351c431402b8461ea51999,310ae3c140ff94b03219ad0adc3c778f,5\r\n31ad1d1b63eb9962463f764d4e6e0c9d,4535b0e1091c278dfd193e5a1d63b39f,4\r\n494dded5b201313c64ed7f100595b95c,d63c1011f49d98b976c352955b1c4bea,5\r\n7711cf624183d843aafe81855097bc37,f177554ea93259a5b282f24e33f65ab6,5\r\nd3e3b74c766bc6214e0c830b17ee2341,99a4788cb24856965c36a24e339b6058,4\r\n19402a48fe860416adf93348aba37

In [2]:
from typing import Dict, Text

import numpy as np
import tensorflow as tf

import tensorflow_recommenders as tfrs

import os
import pprint
import tempfile

import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline

In [ ]:
dataframe = pd.read_csv("/content/jinxpro.csv")
dataframe = dataframe.head(99224)
dataframe[["User_ID", "Product_ID"]] = dataframe[["User_ID", "Product_ID"]].astype(str)
dataframe[["Ratings"]] = dataframe[["Ratings"]].astype(float)
dataframe

User_ID                        Product_ID  \
0      9ef432eb6251297304e76186b10a928d  4244733e06e7ecb4970a6e2683c13e61   
1      b0830fb4747a6c6d20dea0b8c802d7ef  e5f2d52b802189ee658865ca93d83a8f   
2      41ce2a54c0b03bf3443c3d931a367089  c777355d18b72b67abbeef9df44fd0fd   
3      f88197465ea7920adcdbec7375364d82  7634da152a4610f1595efa32f14722fc   
4      8ab97904e6daea8866dbdbc4fb7aad2c  ac6c3623068f30de03045865e4e10089   
...                                 ...                               ...   
99219  67cacf586b432939b6ae2465b2aecf44  13db47eae724e2848e12b71a617a3a41   
99220  4a2c271cbbafa1d8e842cb3975693180  79a564cca1924553af76d396bf7c0662   
99221  e899215e0960eab10aba098c747f2c88  19421075ae0b585f2dc13ff149e2119d   
99222  30ddb50bd22ee927ebe308ea3da60735  19421075ae0b585f2dc13ff149e2119d   
99223  d74f0f48d2cc9237ca21e110142a3cb4  2e7980421ad7946eab8a71b637955704   

       Ratings  
0          4.0  
1          5.0  
2          5.0  
3          5.0  
4          5.0  
...        ...  
99219      5.0  
99220      5.0  
99221      5.0  
99222      4.0  
99223      1.0  

[99224 rows x 3 columns]

In [ ]:
inter_dict = dataframe.groupby(["User_ID", "Product_ID"])["Ratings"].agg(np.mean).reset_index()
inter_dict = {name: np.array(value) for name, value in inter_dict.items()}
interaction = tf.data.Dataset.from_tensor_slices(inter_dict)

prod_dict = dataframe[["Product_ID"]].drop_duplicates()
prod_dict = {name: np.array(value) for name, value in prod_dict.items()}
product = tf.data.Dataset.from_tensor_slices(prod_dict)

interaction = interaction.map(lambda x: {
    "User_ID": x["User_ID"],
    "Product_ID": x["Product_ID"],
    "Ratings": x["Ratings"]
})
product = product.map(lambda x: x["Product_ID"])

In [6]:
#Using movielens datasets
!pip install -q --upgrade tensorflow-datasets
import tensorflow_datasets as tfds

In [7]:
#####
ratings = tfds.load('movielens/100k-ratings', split="train")
movies = tfds.load('movielens/100k-movies', split="train")

# Select the basic features.
ratings = ratings.map(lambda x: {
    "movie_title": x["movie_title"],
    "user_id": x["user_id"],
    "user_rating": x["user_rating"],
})
movies = movies.map(lambda x: x["movie_title"])

Dl Completed...: 0 url [00:00, ? url/s]

Dl Size...: 0 MiB [00:00, ? MiB/s]

Extraction completed...: 0 file [00:00, ? file/s]

Generating splits...:   0%|          | 0/1 [00:00<?, ? splits/s]

Generating train examples...:   0%|          | 0/100000 [00:00<?, ? examples/s]

...

Extraction completed...: 0 file [00:00, ? file/s]

Generating splits...:   0%|          | 0/1 [00:00<?, ? splits/s]

Generating train examples...:   0%|          | 0/1682 [00:00<?, ? examples/s]

Shuffling /root/tensorflow_datasets/movielens/100k-movies/0.1.0.incompleteIBTP44/movielens-train.tfrecord*...:…

Dataset movielens downloaded and prepared to /root/tensorflow_datasets/movielens/100k-movies/0.1.0. Subsequent calls will reuse this data.


In [8]:
######
user_ids = ratings.batch(10_000).map(lambda x: x["user_id"])
product_ids = ratings.batch(10_000).map(lambda x: x["movie_title"])

unique_user = np.unique(np.concatenate(list(user_ids)))
unique_product = np.unique(np.concatenate(list(product_ids)))
print(unique_user)
print(unique_product)

[b'1' b'10' b'100' b'101' b'102' b'103' b'104' b'105' b'106' b'107' b'108'
 b'109' b'11' b'110' b'111' b'112' b'113' b'114' b'115' b'116' b'117'
 b'118' b'119' b'12' b'120' b'121' b'122' b'123' b'124' b'125' b'126'
 b'127' b'128' b'129' b'13' b'130' b'131' b'132' b'133' b'134' b'135'
 b'136' b'137' b'138' b'139' b'14' b'140' b'141' b'142' b'143' b'144'
 b'145' b'146' b'147' b'148' b'149' b'15' b'150' b'151' b'152' b'153'
 b'154' b'155' b'156' b'157' b'158' b'159' b'16' b'160' b'161' b'162'
 b'163' b'164' b'165' b'166' b'167' b'168' b'169' b'17' b'170' b'171'
 b'172' b'173' b'174' b'175' b'176' b'177' b'178' b'179' b'18' b'180'
 b'181' b'182' b'183' b'184' b'185' b'186' b'187' b'188' b'189' b'19'
 b'190' b'191' b'192' b'193' b'194' b'195' b'196' b'197' b'198' b'199'
 b'2' b'20' b'200' b'201' b'202' b'203' b'204' b'205' b'206' b'207' b'208'
 b'209' b'21' b'210' b'211' b'212' b'213' b'214' b'215' b'216' b'217'
 b'218' b'219' b'22' b'220' b'221' b'222' b'223' b'224' b'225' b'226'
 b'227' b

In [10]:
tf.random.set_seed(42)
shuffled = ratings.shuffle(100_000, seed=42, reshuffle_each_iteration=False)

train = shuffled.take(80_000)
test = shuffled.skip(80_000).take(20_000)

cached_train = train.shuffle(100_000).batch(2048)
cached_test = test.batch(4096).cache()

In [19]:
#####
class Model(tfrs.models.Model):
  def __init__(self, rating_weight: float, retrieval_weight: float) -> None:
    super().__init__()

    embed_dim = 32

    self.product_model: tf.keras.layers.Layer = tf.keras.Sequential([
          tf.keras.layers.StringLookup(vocabulary = unique_product, mask_token = None),
          tf.keras.layers.Embedding(len(unique_product) + 1, embed_dim)
    ])

    self.user_model: tf.keras.layers.Layer = tf.keras.Sequential([
          tf.keras.layers.StringLookup(vocabulary = unique_user, mask_token = None),
          tf.keras.layers.Embedding(len(unique_user) + 1, embed_dim)
    ])

    self.rating_model = tf.keras.Sequential([
          tf.keras.layers.Dense(256, activation="relu"),
          tf.keras.layers.Dense(128, activation="relu"),
          tf.keras.layers.Dense(64, activation="relu"),
          tf.keras.layers.Dense(1),
        ])
    
    self.retrieval_task: tf.keras.layers.Layer = tfrs.tasks.Retrieval(
          metrics = tfrs.metrics.FactorizedTopK(
            candidates = movies.batch(128).map(self.product_model)
        )
    )

    self.rating_task: tf.keras.layers.Layer = tfrs.tasks.Ranking(
          loss = tf.keras.losses.MeanSquaredError(),
          metrics = [tf.keras.metrics.RootMeanSquaredError()]
    )

    self.retrieval_weight = retrieval_weight
    self.rating_weight = rating_weight

  def call(self, features: Dict[Text, tf.Tensor]) -> tf.Tensor:
    user_embeddings = self.user_model(features["user_id"])
    product_embeddings = self.product_model(features["movie_title"])
    return(
        user_embeddings, product_embeddings, self.rating_model(tf.concat([user_embeddings, product_embeddings], axis = 1),)
    )

  def compute_loss(self, features: Dict[Text, tf.Tensor], training = False) -> tf.Tensor:
    ratings = features.pop("user_rating")
    user_embeddings, product_embeddings, rating_predictions = self(features)

    retrieval_loss = self.retrieval_task(user_embeddings, product_embeddings)
    rating_loss = self.rating_task(
        labels = ratings,
        predictions = rating_predictions
    )
    return (self.rating_weight * rating_loss + self.retrieval_weight * retrieval_loss)

In [20]:
model = Model(rating_weight=1.0, retrieval_weight=1.0)
model.compile(optimizer=tf.keras.optimizers.Adagrad(0.1))

In [21]:
model.fit(cached_train, epochs=3)
metrics = model.evaluate(cached_test, return_dict=True)

print(f"Retrieval top-100 accuracy: {metrics['factorized_top_k/top_100_categorical_accuracy']:.3f}.")
print(f"Ranking RMSE: {metrics['root_mean_squared_error']:.3f}.")

Epoch 1/3
40/40 [==============================] - 30s 530ms/step - factorized_top_k/top_1_categorical_accuracy: 2.2500e-04 - factorized_top_k/top_5_categorical_accuracy: 0.0064 - factorized_top_k/top_10_categorical_accuracy: 0.0154 - factorized_top_k/top_50_categorical_accuracy: 0.0953 - factorized_top_k/top_100_categorical_accuracy: 0.1874 - root_mean_squared_error: 1.8731 - loss: 14649.0566 - regularization_loss: 0.0000e+00 - total_loss: 14649.0566
Epoch 2/3
40/40 [==============================] - 24s 529ms/step - factorized_top_k/top_1_categorical_accuracy: 7.5000e-04 - factorized_top_k/top_5_categorical_accuracy: 0.0164 - factorized_top_k/top_10_categorical_accuracy: 0.0347 - factorized_top_k/top_50_categorical_accuracy: 0.1671 - factorized_top_k/top_100_categorical_accuracy: 0.2942 - root_mean_squared_error: 1.0594 - loss: 14051.4607 - regularization_loss: 0.0000e+00 - total_loss: 14051.4607
Epoch 3/3
5/5 [==============================] - 8s 964ms/step - factorized_top_k/top_1_

In [32]:
trained_movie_embeddings, trained_user_embeddings, predicted_rating = model({
      "user_id": np.array(["123"]),
      "movie_title": np.array(["Philadelphia Story, The (1940)"])
  })
print("Predicted rating:")
print(predicted_rating)

Predicted rating:
tf.Tensor([[4.245891]], shape=(1, 1), dtype=float32)


In [26]:
retrieval = tfrs.layers.factorized_top_k.BruteForce(model.user_model)
retrieval.index_from_dataset(
    tf.data.Dataset.zip((movies.batch(100), movies.batch(100).map(model.product_model))))

In [29]:
_, titles = retrieval(tf.constant(["123"]))
print(titles)
print(f"Recommendations for user 42: {titles[0, :3]}")

tf.Tensor(
[[b'Annie Hall (1977)' b'Philadelphia Story, The (1940)'
  b'Cinema Paradiso (1988)' b"Antonia's Line (1995)" b'Vertigo (1958)'
  b'Ruby in Paradise (1993)' b'Raise the Red Lantern (1991)'
  b'It Happened One Night (1934)' b'Roman Holiday (1953)'
  b'North by Northwest (1959)']], shape=(1, 10), dtype=string)
Recommendations for user 42: [b'Annie Hall (1977)' b'Philadelphia Story, The (1940)'
 b'Cinema Paradiso (1988)']
